In [1]:
import numpy as np
import pandas as pd
import torch
from torchvision import models, datasets, transforms
import torch.optim as optim
import os
import torch.nn as nn
from torch.utils.data import DataLoader
from torchvision import transforms

from sklearn.utils import shuffle
from sklearn.model_selection import train_test_split
import shutil

In [2]:
disk_folder = 'E:\CodeAlpha\TASK3'
data_folder = 'classification-of-handwritten-letters/'

In [3]:
ls

 Volume in drive E has no label.
 Volume Serial Number is 2622-A609

 Directory of e:\CodeAlpha\TASK3

02/17/2024  04:46 AM    <DIR>          .
02/17/2024  04:46 AM    <DIR>          ..
02/17/2024  04:46 AM             8,955 charcter recognition.ipynb
02/17/2024  04:35 AM    <DIR>          classification-of-handwritten-letters
               1 File(s)          8,955 bytes
               3 Dir(s)  18,305,646,592 bytes free


In [4]:
#perform one-hot encoding (OHE)
def ohe_letter(label):
    result = np.zeros(len(letters))
    index = letters.index(label)
    result[index] = 1
    return result

main_df = pd.read_csv(data_folder + 'letters.csv')
main_df.drop('background', axis=1, inplace=True)

for i in range(len(main_df)):
    main_df['file'][i] = os.path.join('letters', main_df['file'][i])

for root in ['letters2', 'letters3']:
    tmp_df = pd.read_csv(data_folder + root + '.csv')
    tmp_df.drop('background', axis=1, inplace=True)
    for i in range(len(tmp_df)):
        tmp_df['file'][i] = os.path.join(root, tmp_df['file'][i])
    main_df = main_df.merge(tmp_df, how='outer')

main_df = shuffle(main_df)
main_df.head(), main_df.info()

C:\Users\Target\AppData\Local\Temp\ipykernel_9516\3689845541.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  main_df['file'][i] = os.path.join('letters', main_df['file'][i])
C:\Users\Target\AppData\Local\Temp\ipykernel_9516\3689845541.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  main_df['file'][i] = os.path.join('letters', main_df['file'][i])
C:\Users\Target\AppData\Local\Temp\ipykernel_9516\3689845541.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#

<class 'pandas.core.frame.DataFrame'>
Index: 14190 entries, 13547 to 519
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   letter  14190 non-null  object
 1   label   14190 non-null  int64 
 2   file    14190 non-null  object
dtypes: int64(1), object(2)
memory usage: 443.4+ KB


C:\Users\Target\AppData\Local\Temp\ipykernel_9516\3689845541.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tmp_df['file'][i] = os.path.join(root, tmp_df['file'][i])
C:\Users\Target\AppData\Local\Temp\ipykernel_9516\3689845541.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tmp_df['file'][i] = os.path.join(root, tmp_df['file'][i])
C:\Users\Target\AppData\Local\Temp\ipykernel_9516\3689845541.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-vi

(      letter  label                 file
 13547      ь     30  letters3\30_388.png
 10049      л     13  letters3\13_290.png
 9934       к     12  letters3\12_375.png
 2910       ж      8   letters2\08_51.png
 6573       ъ     28  letters2\28_114.png,
 None)

In [5]:
#associate each image file with its corresponding one-hot encoded label
letters = ''
name_of_letters = ['filename']
for letter in main_df.letter.unique():
    letters += letter
    name_of_letters.append(letter)

labels = main_df.label

classnames = [i for i in letters]

inputs = main_df['letter'].apply(ohe_letter)
a = []
for i in range(len(inputs)):
    t = [main_df.file.values[i]]
    for q in inputs[i]:
        t.append(q)
    a.append(t)

main_df = shuffle(pd.DataFrame(a, columns = name_of_letters))

In [6]:
for Class in classnames:
    for phase in ['train', 'valid']:
        os.makedirs(os.path.join(disk_folder, phase, Class))

In [7]:
train_df, valid_df = train_test_split(main_df, test_size=0.15, random_state=42)

In [8]:
for index, row in train_df.iterrows():
    for bukv in classnames:
        if row[bukv]:
            shutil.copy(os.path.join(data_folder, row['filename']), os.path.join(disk_folder, 'train', bukv))

for index, row in valid_df.iterrows():
    for bukv in classnames:
        if row[bukv]:
            shutil.copy(os.path.join(data_folder, row['filename']), os.path.join(disk_folder, 'valid', bukv))

In [9]:
data_transforms = {
    'train':
    transforms.Compose([
        transforms.Resize((32, 32)),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406],std=[0.229, 0.224, 0.225])
    ]),
    'valid':
    transforms.Compose([
        transforms.Resize((32, 32)),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406],std=[0.229, 0.224, 0.225])
    ]),
}

In [10]:
image_datasets = {
    'train':
    datasets.ImageFolder(os.path.join(disk_folder), data_transforms['train']),

    'valid':
    datasets.ImageFolder(os.path.join(disk_folder), data_transforms['valid'])
}


In [11]:

dataloaders = {
    'train':
    DataLoader(image_datasets['train'],
              batch_size=16,
              shuffle=True,
              num_workers=0),
    
    'valid':
    DataLoader(image_datasets['valid'],
              batch_size=16,
              shuffle=True,
              num_workers=0)
}

In [12]:
device = torch.device('cuda:0' if torch.cuda.is_available() else "cpu")

model = models.resnet18(pretrained=False).to(device)

model.fc = nn.Linear(model.fc.in_features, 33).to(device)

C:\Users\Target\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\torchvision\models\_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
C:\Users\Target\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)


In [13]:
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.fc.parameters())

In [14]:
from tqdm import tqdm

def train_model(model, criterion, optimizer, num_epochs=3):
    for epoch in range(num_epochs):
        print('Epoch {}/{}'.format(epoch+1, num_epochs))
        print('-' * 10)

        for phase in ['train', 'valid']:
            if phase == 'train':
                model.train()
            else:
                model.eval()

            running_loss = 0.0
            running_corrects = 0

            for inputs, labels in tqdm(dataloaders[phase], total=len(dataloaders[phase])):
                inputs = inputs.to(device)
                labels = labels.to(device)

                outputs = model(inputs)
                loss = criterion(outputs, labels)

                if phase == 'train':
                    optimizer.zero_grad()
                    loss.backward()
                    optimizer.step()

                _, preds = torch.max(outputs, 1)
                running_loss += loss.item() * inputs.size(0)
                running_corrects += torch.sum(preds == labels.data)

            epoch_loss = running_loss / len(dataloaders[phase])
            epoch_acc = running_corrects.double() / len(dataloaders[phase])

            print('{} loss: {:.4f}, acc: {:.4f}'.format(phase,
                                                        epoch_loss,
                                                        epoch_acc))
    return model

In [15]:
trained_model = train_model(model, criterion, optimizer, num_epochs=5)


Epoch 1/5
----------


100%|██████████| 4106/4106 [18:44<00:00,  3.65it/s]


train loss: 10.0327, acc: 12.2986


100%|██████████| 4106/4106 [03:45<00:00, 18.23it/s]


valid loss: 9.5653, acc: 12.5200
Epoch 2/5
----------


...

valid loss: 9.8010, acc: 12.0329
Epoch 5/5
----------


100%|██████████| 4106/4106 [12:37<00:00,  5.42it/s]


train loss: 9.9076, acc: 12.3334


100%|██████████| 4106/4106 [02:59<00:00, 22.85it/s]

valid loss: 10.0106, acc: 12.5375
